## Workbook Set-up

In [403]:
# Packages
import numpy as np
import math
import csv
from datetime import datetime

import torch
import torch.nn as nn
import torch.optim as optim

import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from sklearn.model_selection import TimeSeriesSplit

In [404]:
device = "cuda" if torch.cuda.is_available() else "cpu"
torch.cuda.is_available()

True

## Data Wrangling

### Data Import, Filtering, & Formatting

In [405]:
# Data Import
file = 'Service_Calls_All.csv'

with open(file, mode='r') as file:
    csv_reader = csv.reader(file)
    header = next(csv_reader)
    data = [row for row in csv_reader]

In [406]:
# Training Columns
crime_code = header.index('Incident Type Code')
crime_type = header.index('Classification')
incident_date = header.index('Incident date')
latitude = header.index('Latitude')
longitude = header.index('Longitude')

train_cols = [crime_code, crime_type, incident_date, latitude, longitude]
train_col_names = ['Incident_Type_Code', 'Classification', 'Incident_Date', 'Latitude', 'Longitude']

In [407]:
# Filter Data
## Columns
service_calls = [[row[i] for i in train_cols] for row in data]

## Rows
violent_crimes_types = ['Robbery', 'Assault/Battery', 'Homicide', 'Kidnap']
violent_crimes = []
for rows in service_calls:
    if rows[1] in violent_crimes_types:
        violent_crimes.append(rows)

In [408]:
date_format = '%m/%d/%Y %I:%M:%S %p'
# Data Type
violent_crimes_dtype = []
n=0
for row in violent_crimes:
    try:
        if not isinstance(row[2], datetime):
            date = datetime.strptime(row[2], date_format)
        else:
            date = row[2]
        lat = float(row[3])
        long = float(row[4])
        
        temp_list = [row[0], row[1], date, lat, long]
        violent_crimes_dtype.append(temp_list)
    except ValueError as e:
        print(f"Error parsing row {row}: {e}")
violent_crimes = violent_crimes_dtype

In [409]:
# Total Service Calls
print('Total Service Calls: ', len(service_calls))
print('Total Violent Calls: ', len(violent_crimes))
print(f'Violent Call Percentage: {len(violent_crimes)/len(service_calls)*100:.3}%')

Total Service Calls:  1345306
Total Violent Calls:  84163
Violent Call Percentage: 6.26%


In [414]:
print(train_col_names)
for row in violent_crimes[0:3]:
    print(row)

['Incident_Type_Code', 'Classification', 'Incident_Date', 'Latitude', 'Longitude']
['407', 'Robbery', datetime.datetime(2019, 3, 13, 23, 17, 12), 36.10083146, -115.13836994]
['407', 'Robbery', datetime.datetime(2019, 2, 22, 10, 20, 59), 36.18825788, -115.20608379]
['407', 'Robbery', datetime.datetime(2019, 8, 26, 3, 47, 25), 36.15107941, -115.05890844]


### Totals by Group

In [381]:
# Unique Lists
month_year = []
years = []
dates = []

for row in violent_crimes:
    dates.append(row[2].date())
    month_year.append(datetime(row[2].year, row[2].month, 1))
    years.append(row[2].year)

# Unique Values and Sort
dates = list(set(dates))
dates.sort()
month_year = list(set(month_year))
month_year.sort()
years = list(set(years))
years.sort()

# Totals
# By Date
daily_count = np.zeros(len(dates))

for row in violent_crimes:
    day_index = dates.index(row[2].date())
    daily_count[day_index] += 1

daily_crime_totals = {
    'Date': dates,
    'Crime_Count': daily_count
}

# Totals
# By Month/Year
monthly_count = np.zeros(len(month_year))

for row in violent_crimes:
    month_index = month_year.index(datetime(row[2].year, row[2].month, 1))
    monthly_count[month_index] += 1

monthly_crime_totals = {
    'Month_Year': month_year,
    'Crime_Count': monthly_count
}

# By Year
yearly_count = np.zeros(len(years))

for row in violent_crimes:
    year_index = years.index(row[2].year)
    yearly_count[year_index] += 1

yearly_crime_totals = {
    'Year': years,
    'Crime_Count': yearly_count
}

## By Day of the Week
day_num = np.zeros(7, dtype=int)
day_name = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']

for row in violent_crimes:
    day_ind = row[2].weekday()
    day_num[day_ind-1] += 1

weekday_crimes = {'Day': day_name,
                  'Crime_Count':day_num}

## By Month of the Year
month_num = np.zeros(12, dtype=int)
month_name = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']

for row in violent_crimes:
    month_ind = row[2].month
    month_num[month_ind-1] += 1

month_crimes = {'Month': month_name,
                  'Crime_Count':month_num}

### Positional Data

In [382]:
# Lat/Long Ranges
latitude = []
longitude = []
for p in service_calls:
    latitude.append(float(p[3]))
    longitude.append(float(p[4]))
    
min_lat = min(latitude)
max_lat = max(latitude)
print('Latitude ')
print(f'Range: ({min_lat}, {max_lat})')

min_long = min(longitude)
max_long = max(longitude)
print('\nLongitude ')
print(f'Range: ({min_long}, {max_long})')

Latitude 
Range: (35.01617255, 37.0)

Longitude 
Range: (-116.0, -114.05437268)


In [383]:
# Chosen Grid Corners
lat = [36.18, 36.32, 36.19, 35.96]
long = [-115.37, -115.22, -115.01, -115.18]

lat_range = [min(lat), max(lat)]
long_range = [min(long), max(long)]
print('Latidue ', lat_range)
print('Longitude ', long_range)

Latidue  [35.96, 36.32]
Longitude  [-115.37, -115.01]


North - (36.322147985233215, -115.22048782134914)  
East - (36.19078549533123, -115.01471375825048)  
South - (35.96155626159423, -115.18082383622412)  
West - (36.17760414416091, -115.37073555042826)  

In [384]:
# Lat/Long Segmentation Groups
lat_steps = list(np.round(np.arange(lat_range[0], lat_range[1], .01), 2))
long_steps = list(np.round(np.arange(long_range[0], long_range[1], .01), 2))

print('Latitude Grid Blocks:', len(lat_steps))
print('Longitude Grid Blocks:', len(long_steps))

# Function to truncate lat/long to 2 decimals
def truncate_to_decimals(value, decimals):
    factor = 10 ** decimals
    return int(value * factor) / factor


# Count Crime by Grid Block
map_matrix = np.zeros((len(lat_steps),len(long_steps)), dtype=int)

for row in violent_crimes:
    try:
        i = lat_steps.index(truncate_to_decimals(row[3],2))
        j = long_steps.index(truncate_to_decimals(row[4],2))
        map_matrix[i,j] += 1
    except:
        pass


# Count Crime by Grid Block and Date
date_matrix = np.zeros((len(dates), len(lat_steps), len(long_steps)), dtype=int)

for row in violent_crimes:
    try:
        # Lat
        i = lat_steps.index(truncate_to_decimals(row[3],2))
        # Long
        j = long_steps.index(truncate_to_decimals(row[4],2))
        # Date
        k = dates.index(row[2].date())
        date_matrix[k,i,j] += 1
    except:
        pass


# Count Crime by Grid Block and Month/Year
monthyear_matrix = np.zeros((len(month_year), len(lat_steps), len(long_steps)), dtype=int)

for row in violent_crimes:
    try:
        # Lat
        i = lat_steps.index(truncate_to_decimals(row[3],2))
        # Long
        j = long_steps.index(truncate_to_decimals(row[4],2))
        # Date
        k = month_year.index(datetime(row[2].year, row[2].month, 1))
        monthyear_matrix[k,i,j] += 1
    except:
        pass

# Crime Counts by Grid Block and Day of the Week
day_matrix = np.zeros((len(day_num), len(lat_steps), len(long_steps)), dtype=int)

for row in violent_crimes:
    try:
        # Lat
        i = lat_steps.index(truncate_to_decimals(row[3],2))
        # Long
        j = long_steps.index(truncate_to_decimals(row[4],2))
        # Date
        k = row[2].weekday()-1
        day_matrix[k,i,j] += 1
    except:
        pass

# Crime Counts by Grid Block and Month of the Year
month_matrix = np.zeros((len(month_num), len(lat_steps), len(long_steps)), dtype=int)

for row in violent_crimes:
    try:
        # Lat
        i = lat_steps.index(truncate_to_decimals(row[3],2))
        # Long
        j = long_steps.index(truncate_to_decimals(row[4],2))
        # Date
        k = row[2].month-1
        month_matrix[k,i,j] += 1
    except:
        pass

Latitude Grid Blocks: 36
Longitude Grid Blocks: 36


## Plotting

In [385]:
# Daily - Crime Counts
fig = px.line(
    daily_crime_totals,
    x='Date',
    y='Crime_Count'
)
fig.update_layout(
    title = 'Daily Violent Crime Totals',
    xaxis_title = 'Date',
    yaxis_title = 'Count',
    height = 500,
    width = 2000
)
fig.show()

In [386]:
# Daily - Crime Counts
fig = px.line(
    monthly_crime_totals,
    x='Month_Year',
    y='Crime_Count'
)
fig.update_layout(
    title = 'Monthly Violent Crime Totals',
    xaxis_title = 'Date',
    yaxis_title = 'Count',
    height = 500,
    width = 2000
)
fig.show()

In [387]:
# Crime Counts by Day of the Week
fig = px.bar(
    weekday_crimes,
    x = 'Day',
    y = 'Crime_Count',
    text = 'Crime_Count',

)
fig.update_layout(
    title = 'Crime Counts by Day of the Week',
    xaxis_title = 'Day',
    yaxis_title = 'Count',
    height = 500,
    width = 1000
)
fig.show()

In [388]:
# Crime Counts by Month of the Year
fig = px.bar(
    month_crimes,
    x = 'Month',
    y = 'Crime_Count',
    text = 'Crime_Count',

)
fig.update_layout(
    title = 'Crime Counts by Month of the Year',
    xaxis_title = 'Month',
    yaxis_title = 'Count',
    height = 500,
    width = 1000
)
fig.show()

In [389]:
# Heat Map - Day of the Week
fig = make_subplots(
    rows=1, 
    cols=7,
    subplot_titles= day_name,
    horizontal_spacing=0.02
    )

zmax = day_matrix.max()
for i, d in enumerate(day_matrix):
    fig.add_trace(go.Heatmap(z=d, zmin=0, zmax=zmax,showscale=True, colorscale='thermal'), row=1, col=i+1)

fig.update_layout(
    title = 'Heat Map - Day of the Week',
    height = 400,
    width = 2100
)

fig.show()

In [390]:
# Heat Map - Day of the Week
fig = make_subplots(
    rows=3, 
    cols=4,
    subplot_titles= month_name,
    vertical_spacing=0.05,
    horizontal_spacing=0.02
    )

zmax = month_matrix.max()
for i, m in enumerate(month_matrix):
    if i<=3:
        fig.add_trace(go.Heatmap(z=m, zmin=0, zmax=zmax, showscale=True, colorscale='thermal'), row=1, col=i+1)
    elif i<=7:
        fig.add_trace(go.Heatmap(z=m, zmin=0, zmax=zmax, showscale=False, colorscale='thermal'), row=2, col=i-3)
    else:
        fig.add_trace(go.Heatmap(z=m, zmin=0, zmax=zmax, showscale=False, colorscale='thermal'), row=3, col=i-7)
fig.update_layout(
    title = f'Heat Map - Month of the Year',
    height = 1000,
    width = 1500,
)

fig.show()

In [391]:
# Map Violent Crimes to Dictionary
service_dict = {key: [] for key in train_col_names}
for row in violent_crimes:
    for i in range(5):
        service_dict[train_col_names[i]].append(row[i])

In [392]:
# Heat Map
fig = px.density_mapbox(
    lat = service_dict['Latitude'], lon = service_dict['Longitude'], z = np.ones(len(violent_crimes)),
    radius = 25,
    center = dict(lat = 36.13, lon = -115.17),
    zoom = 9.5,
    mapbox_style = 'open-street-map',
    color_continuous_scale = 'thermal',
    opacity = 0.8,
    range_color = (0,700)
)

fig.update_layout(
    title = f'Las Vegas Heat Map ({min(years)}-{max(years)}) - Raw Data ',
    height = 800,
    width = 1000,
)

fig.show() 

In [393]:
# Remap Grid back to dictionary
## Grids
lat_list = []
long_list = []
crime_total = []

for i in range(map_matrix.shape[0]):
    for j in range(map_matrix.shape[0]):
        lat_list.append(lat_steps[i]+.005)
        long_list.append(long_steps[j]+.005)
        crime_total.append(map_matrix[i,j])

alltime_totals_grid = {
    'lat': lat_list,
    'long': long_list,
    'crime_total': crime_total,
}

In [418]:
# Heat Map
fig = px.density_mapbox(
    lat = alltime_totals_grid['lat'], lon = alltime_totals_grid['long'], z = alltime_totals_grid['crime_total'],
    radius = 30,
    center = dict(lat = 36.13, lon = -115.17),
    zoom = 9.5,
    mapbox_style = 'open-street-map',
    color_continuous_scale = 'thermal',
    opacity = 0.7,
    range_color = (0,max(crime_total)*.4)
)

fig.update_layout(
    title = f'Las Vegas Crime Heat Map ({min(years)}-{max(years)}) - Grid Smoothing',
    height = 800,
    width = 1000,
)

fig.show()

# Cell Statistics
print('Cell Statistics:')
print(f' Min = {np.min(crime_total)}')
print(f' Max = {np.max(crime_total)}')
print(f' Mean = {np.mean(crime_total):.2f}')
print(f' Median = {np.median(crime_total):.2f}')
print(f' Standard Deviation = {np.std(crime_total):.2f}')

Cell Statistics:
 Min = 0
 Max = 2601
 Mean = 63.26
 Median = 10.00
 Standard Deviation = 162.76
